CODE FOR FETCHING FROM A SINGLE DISEASE FROM THE CONSTRUCTED URLS

In [157]:
import requests
from bs4 import BeautifulSoup

def fetch_qa(url):
  res = requests.get(url)
  html = res.text
  soup = BeautifulSoup(html, "html.parser")
  accordion = soup.find("div", id="sf-accordion")
  qa_pairs = []

  for panel in accordion.find_all(
    "div",
    class_="sf-accordion__panel",
    itemtype="https://schema.org/Question"
  ):
    q_tag = panel.find("span", itemprop="name")
    question = q_tag.get_text(strip=True) if q_tag else None
    a_tag = panel.find("div", itemprop="text")
    answer = a_tag.get_text(separator=" ", strip=True) if a_tag else None

    if question and answer:
        qa_pairs.append({
            "question": question,
            "answer": answer
        })

  return qa_pairs




In [158]:


# base_url = "https://www.who.int/news-room/questions-and-answers/item/ebola-disease"
# t=fetch_qa(base_url)
# print(t)


In [159]:

# accordion_div

This is the api

In [160]:
base_api="https://www.who.int/api/hubs/qandagroups"
params = {
    "sf_site": "15210d59-ad60-47ff-a542-7ed76645f0c7",
    "sf_provider": "OpenAccessProvider",
    "sf_culture": "en",
    "$orderby": "PublicationDateAndTime desc",
    "$select": "Title,ItemDefaultUrl,FormatedDate",
    "$format": "json",
    "$top": 20,
    "$skip": 0,
    "$count": "true"
}


In [161]:
all_items = []
skip = 0
top = params["$top"]

while True:
    params["$skip"] = skip
    res = requests.get(base_api, params=params, timeout=10)
    res.raise_for_status()

    data = res.json()
    items = data.get("value", [])

    if not items:
        break

    all_items.extend(items)
    skip += top

print(f"Fetched {__builtins__.len(all_items)} items")

Fetched 332 items


In [190]:
all_items
urls=[i["ItemDefaultUrl"]for i in all_items]

In [191]:
#contain all diseases
# urls
qa={}

In [192]:
base="https://www.who.int/news-room/questions-and-answers/item"
len=0
for i in urls:
  new_url=base+i
  if i not in qa:
    qa[i] = []
  qa[i].append((fetch_qa(new_url)))
  print(f"done"+i)

  len+=1
print(len)

done/ebola-disease
done/q-a-on-rts-s-malaria-vaccine
done/malaria
done/obesity-glp-1-therapies
done/traditional-medicine
done/tuberculosis
done/vaccines-and-immunization-what-is-vaccination
done/ebola-vaccines
done/who-as-an-accredited-entity-of-the-adaptation-fund
done/vaccines-and-immunization-vaccine-safety
done/autism-spectrum-disorders-(asd)
done/workplace-heat-stress
done/neglected-tropical-diseases-paragonimiasis
done/neglected-tropical-diseases-opisthorchiasis
done/echinococcosis
done/q-a-on-fascioliasis
done/neglected-tropical-diseases-clonorchiasis
done/taeniasis-and-cysticercosis
done/chikungunya
done/use-of-potassium-iodine-for-thyroid-protection-during-nuclear-or-radiological-emergencies
done/who-unicef-estimates-of-national-immunization-coverage
done/social-connection
done/pandemic-prevention--preparedness-and-response-accord
done/respiratory-syncytial-virus-(rsv)-immunization-products
done/q-a-who-handbook-for-national-quality-policy-and-strategy
done/mononucleosis-(glan

In [193]:
qa


{'/ebola-disease': [[{'question': 'What is Ebola disease?',
    'answer': 'Ebola disease is a rare but severe illness, caused by a virus belonging to the genus orthoebolavirus of the Filoviridae family. Death rates have varied from 25% to 90% in past outbreaks. Six species of orthoebolaviruses have been identified to date, with three known to cause large outbreaks: Ebola virus (EBOV) causing Ebola virus disease (EVD) Sudan virus (SUDV) causing Sudan virus disease (SVD) Bundibugyo virus (BDBV) causing Bundibugyo virus disease (BVD). The animal reservoir of the viruses is unknown, but current evidence suggests that fruit bats ( Pteropodidae ) may be a host.'},
   {'question': 'What are the typical symptoms of Ebola disease?',
    'answer': 'The symptoms of Ebola disease can be sudden and can include: fever fatigue muscle pain headache and sore throat. These can be followed by: vomiting diarrhoea rash internal and external bleeding.'},
   {'question': 'How long does it take for people to 

In [214]:

with open("train.jsonl", "w", encoding="utf-8") as f:

  for key,value in qa.items():
    inner_list=value[0]
    for j in inner_list:
      record = {
        "topic": key,
        "question": j["question"],
        "answer": j["answer"]
      }
      f.write(json.dumps(record, ensure_ascii=False) + "\n")


<_io.TextIOWrapper name='train.jsonl' mode='w' encoding='utf-8'>

In [212]:
qa

{'/ebola-disease': [[{'question': 'What is Ebola disease?',
    'answer': 'Ebola disease is a rare but severe illness, caused by a virus belonging to the genus orthoebolavirus of the Filoviridae family. Death rates have varied from 25% to 90% in past outbreaks. Six species of orthoebolaviruses have been identified to date, with three known to cause large outbreaks: Ebola virus (EBOV) causing Ebola virus disease (EVD) Sudan virus (SUDV) causing Sudan virus disease (SVD) Bundibugyo virus (BDBV) causing Bundibugyo virus disease (BVD). The animal reservoir of the viruses is unknown, but current evidence suggests that fruit bats ( Pteropodidae ) may be a host.'},
   {'question': 'What are the typical symptoms of Ebola disease?',
    'answer': 'The symptoms of Ebola disease can be sudden and can include: fever fatigue muscle pain headache and sore throat. These can be followed by: vomiting diarrhoea rash internal and external bleeding.'},
   {'question': 'How long does it take for people to 

{"topic": "/long-term-studies-on-children-s-health-and-the-environment-how-can-we-identify-assess-and-follow-up-the-effects-of-exposure-to-environmental-factors", "question": "What was the outcome of the Montreux consultation in October 2003, in Switzerland ?", "answer": "WHO and the International Interest Group organized an informal consultation on the Feasibility of Long Term Studies (LTS) in the Environment Threats to the Health of Children in Developing Countries, October 13-15, 2003 in Montreux, Switzerland. Participants of the meeting discussed the need and feasibility of conducting LTS in developing and transition countries. They strongly endorsed the inclusion of environmental issues in LTS and the resultant \"White Paper\" is available here ."}
